# Intersection simulation
### Jorge Alejandro López Sosa - A01637313
## Link to Github: [Github](https://github.com/jloftw/MultiAgent_Activities)

## Rules

- As long as there is no vehicle nearby, the traffic light will be yellow.
- When a vehicle approaches the intersection, it will send a message with the estimated time of arrival.
- The traffic light will give the green light to the nearest traffic light and will establish a light program from that point on for the rest of the vehicles.

## Agents Involved
- Car
- Traffic Light

## Interaction
- The car should be able to see what color the traffic light ahead of it is.
- The traffic light should be able to detect cars that are moving towards it and change its color accordingly.

## Imports

In [1]:
import agentpy as ap
import matplotlib.pyplot as plt
import IPython
from random import choice
import itertools
from enum import Enum

## Create Types

In [2]:
class Valid_Moves(Enum):
    LEFT_RIGHT = (0, 1)
    UP_DOWN = (1, 0)

class Colors(Enum):
    YELLOW = 1
    GREEN = 2
    RED = 3
    PURPLE = 4

## Create Car agent

In [3]:
class CarAgent(ap.Agent):
    def setup(self):
        self.current_move_type = choice(list(Valid_Moves))
        self.has_light = False
    
    def move(self):
        if self.check_can_pass(self.current_move_type.value):
            self.model.street.move_by(self, self.current_move_type.value)
        
        if not self.has_light:
            self.check_light()
        else:
            self.check_passed_light()
    
    # Check the traffic light ahead
    def check_light(self):
        width = self.model.width
        height = self.model.height
        pos = self.model.street.positions[self]
        
        if self.current_move_type in (Valid_Moves.UP_DOWN, Valid_Moves.LEFT_RIGHT):
            for i in range(pos[0], height):
                for agent in self.model.street.agents[i, pos[1]]:
                    if agent.type == "TrafficLightAgent":
                        self.has_light = True
                        agent.add_car()
                        return
        else:
            for i in range(pos[1], width):
                for agent in self.model.street.agents[pos[0], i]:
                    if agent.type == "TrafficLightAgent":
                        self.has_light = True
                        agent.add_car()
                        return
    
    # Check if the car has passed the traffic light
    def check_passed_light(self):
        pos = self.model.street.positions[self]

        for agent in self.model.street.agents[pos]:
            if agent.type == "TrafficLightAgent":
                self.has_light = False
                agent.remove_car()
                break
    
    # Get new position for car
    def get_new_pos(self, move):
        pos = self.model.street.positions[self]

        return tuple(map(sum, zip(pos, move)))

    # Check if car can move to position (if traffic light is red or there is another car)
    def check_can_pass(self, move):
        width = self.model.width
        height = self.model.height
        new_pos = self.get_new_pos(move)

        for agent in self.model.street.agents[new_pos[0] % height, new_pos[1] % width]:
            if agent.type == 'TrafficLightAgent' and agent.is_red():
                return False
            if agent.type == 'CarAgent':
                return False
        
        return True

## Create Traffic Light agent

In [4]:
class TrafficLightAgent(ap.Agent):
    def setup(self):
        self.light_color = Colors.YELLOW
        self.green_time = 0
        self.red_time = 0
        self.cars = 0
        self.time = 15

    # Add cars so that the traffic light can change the time that it takes to change colors
    def add_car(self):
        self.cars += 1
    
    # Remove the cars after they are no longer relevant to the traffic light
    def remove_car(self):
        if self.cars > 0:
            self.cars -= 1

        # change traffic light to yellow if there are no cars present
        if self.cars == 0:
            self.change_to_yellow()

    # Reduce the time it takes to change colors if there are more cars
    def reduce_time(self):
        if self.cars == 0:
            self.change_to_yellow()

        pos = self.model.street.positions[self]

        if self.is_yellow():
            for agent in self.model.street.agents[pos[0] - 1, pos[1] + 1]:
                if agent.type == "TrafficLightAgent" and agent.is_green():
                    self.change_to_red(self.time)
                    return
                elif agent.type == "TrafficLightAgent" and self.cars > 0:
                    self.change_to_green(self.time)
                    return
            
            for agent in self.model.street.agents[pos[0] + 1, pos[1] - 1]:
                if agent.type == "TrafficLightAgent" and agent.is_green():
                    self.change_to_red(self.time)
                    return
                elif agent.type == "TrafficLightAgent" and self.cars > 0:
                    self.change_to_green(self.time)
                    return
        elif self.is_red():
            if self.red_time > 0:
                self.red_time -= 1
                return

            for agent in self.model.street.agents[pos[0] - 1, pos[1] + 1]:
                if agent.type == "TrafficLightAgent" and self.red_time <= 0:
                    agent.change_to_red()
                    self.change_to_green()
                    return
            
            for agent in self.model.street.agents[pos[0] + 1, pos[1] - 1]:
                if agent.type == "TrafficLightAgent" and self.red_time <= 0:
                    agent.change_to_red()
                    self.change_to_green()
                    return
        else:
            if self.green_time > 0:
                self.green_time -= 1
                return
            
            for agent in self.model.street.agents[pos[0] - 1, pos[1] + 1]:
                if agent.type == "TrafficLightAgent" and self.red_time <= 0:
                    agent.change_to_green()
                    self.change_to_red(self.time)
                    return
            
            for agent in self.model.street.agents[pos[0] + 1, pos[1] - 1]:
                if agent.type == "TrafficLightAgent" and self.red_time <= 0:
                    agent.change_to_green()
                    self.change_to_red(self.time)
                    return
    
    # Change the traffic light color to red
    def change_to_red(self, time = 0):
        if time == 0: time = self.time
        if self.light_color != Colors.RED:
            self.red_time = time
            self.light_color = Colors.RED
            self.color = self.light_color.value

    # Change the traffic light color to green
    def change_to_green(self, time = 0):
        if time == 0: time = self.time
        if self.light_color != Colors.GREEN:
            self.green_time = time
            self.light_color = Colors.GREEN
            self.color = self.light_color.value
    
    # Change the traffic light color to yellow
    def change_to_yellow(self):
        self.green_time = 0
        self.red_time = 0
        self.light_color = Colors.YELLOW
        self.color = self.light_color.value
    
    # Check if traffic light color is green
    def is_green(self):
        return self.light_color == Colors.GREEN

    # Check if traffic light color is yellow
    def is_yellow(self):
        return self.light_color == Colors.YELLOW

    # Check if traffic light color is red
    def is_red(self):
        return self.light_color == Colors.RED

## Create Intersection Model

In [5]:
class IntersectionModel(ap.Model):
    def setup(self):
        x_separations = self.p.lights_separation["X"]
        y_separations = self.p.lights_separation["Y"]

        self.width = int(self.p["size"][0])
        self.height = int(self.p["size"][1])

        x_positions = range(x_separations, self.height, x_separations)
        y_positions = range(y_separations, self.width, y_separations)

        # create lights
        lights_locations = list(itertools.product(x_positions, y_positions))
        lights_locations = [(location[0], location[1] - 1) for location in lights_locations] + [(location[0] - 1, location[1]) for location in lights_locations]

        n_lights = len(lights_locations)
        self.lights = ap.AgentList(self, n_lights, TrafficLightAgent)

        # create cars
        n_cars = int(self.p["cars"])
        self.cars = ap.AgentList(self, n_cars, CarAgent)

        # color for agents
        self.lights.color = Colors.YELLOW.value
        self.cars.color = Colors.PURPLE.value

        self.lights.time = 15

        # create streets
        self.street = ap.Grid(self, [self.width, self.height], track_empty=True, torus=True)

        # add lights to model
        self.street.add_agents(self.lights, lights_locations)

        # add cars to model
        valid_spawn_points = [(0, x) for x in x_positions] + [(y, 0) for y in y_positions]

        spawn_points = [choice(valid_spawn_points) for _ in self.cars]

        self.spawn_cars(spawn_points)

    # Add cars and assign their movement type
    def spawn_cars(self, spawn_points):
        for car, spawn_point in zip(self.cars, spawn_points):
            if spawn_point[0] == 0:
                car.current_move_type = Valid_Moves.UP_DOWN
            elif spawn_point[1] == 0:
                car.current_move_type = Valid_Moves.LEFT_RIGHT
        
        self.street.add_agents(self.cars, spawn_points)

    def step(self):
        for car in self.cars:
            car.move()
        
        for light in self.lights:
            light.reduce_time()

    def end(self):
        pass

## Create parameters for animation

In [6]:
parameters = {
    "size": [50, 50],
    "cars": 50,
    "lights_separation": {"X": 10, "Y": 10},
    "steps": 500,
}

## Animation

In [7]:
def animation_plot(model, ax):
    attr_grid = model.street.attr_grid('color')
    color_dict = {Colors.PURPLE.value:'#A020F0', Colors.RED.value:'#FF0000', Colors.YELLOW.value:'#FFFF00', Colors.GREEN.value:'#00FF00', None:'#000000'}
    ap.gridplot(attr_grid, ax=ax, color_dict=color_dict, convert=True)
    ax.set_title(f"Simulation of Traffic\n"
                 f"Time-step: {model.t}")

fig, ax = plt.subplots() 
model = IntersectionModel(parameters)
animation = ap.animate(model, fig, ax, animation_plot)
IPython.display.HTML(animation.to_jshtml(fps=30))